In [8]:
SCOPETYPE = 'OPENADC'
PLATFORM = 'CWLITEXMEGA'
SS_VER = 'SS_VER_2_1'
%run "../../Setup_Scripts/Setup_Generic.ipynb"

INFO: Found ChipWhisperer😍
<class 'chipwhisperer.capture.api.programmers.XMEGAProgrammer'>
scope.adc.offset                         changed from 73700                     to 0                        
scope.adc.samples                        changed from 3000                      to 5000                     
scope.clock.adc_freq                     changed from 86972785                  to 30185691                 
scope.clock.adc_rate                     changed from 86972785.0                to 30185691.0               


In [2]:
%%bash -s "$PLATFORM" "$SS_VER"
cd ../../../hardware/victims/firmware/simpleserial-des
make PLATFORM=$1 CRYPTO_TARGET=AVRCRYPTOLIB  SS_VER=$2 -j

SS_VER set to SS_VER_2_1
SS_VER set to SS_VER_2_1
.
Size after:
+--------------------------------------------------------
avr-gcc (Homebrew AVR GCC 9.4.0) 9.4.0
Copyright (C) 2019 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

Welcome to another exciting ChipWhisperer target build!!
+ Built for platform CW-Lite XMEGA with:
   text	   data	    bss	    dec	    hex	filename
   4652	      8	     82	   4742	   1286	simpleserial-des-CWLITEXMEGA.elf
+ CRYPTO_TARGET = AVRCRYPTOLIB
+ CRYPTO_OPTIONS = DES
+--------------------------------------------------------


In [3]:
fw_path = f"/Users/alex/Documents/ChipWhisperer/chipwhisperer/hardware/victims/firmware/simpleserial-des/simpleserial-des-{PLATFORM}.hex"
print(fw_path)
prog = cw.programmers.XMEGAProgrammer
cw.program_target(scope, prog, fw_path)


/Users/alex/Documents/ChipWhisperer/chipwhisperer/hardware/victims/firmware/simpleserial-des/simpleserial-des-CWLITEXMEGA.hex
XMEGA Programming flash...
XMEGA Reading flash...
Verified flash OK, 4659 bytes


We'll probably crash the target a few times while we're trying some glitching. Create a function to reset the target:

In [4]:
def reboot_flush():            
    scope.io.pdic = False
    time.sleep(0.1)
    scope.io.pdic = "high_z"
    time.sleep(0.1)
    #Flush garbage too
    target.flush()

In [5]:
def print_output(returned_data):
    print(returned_data)
    print(f'Cmd: {chr(returned_data[1])}')
    print(f'Len: {returned_data[2]}')
    print(f'Payload (hex): {returned_data[3:-2].hex(" ",1).upper()}')

In [6]:
def capture_traces(cmd, data):
    target.flush()
    scope.arm()
    target.send_cmd(cmd, 0, data)
    capture = scope.capture()
    if capture:
        print("Timeout")
    data = target.read_cmd('r')
    trace = scope.get_last_trace()
    return data, trace

In [9]:
from tqdm.notebook import trange
import numpy as np

# Create project to save traces to
project = cw.create_project("projects/des", overwrite = True)

reboot_flush()

# Display the actual key
target.send_cmd("x", 0, [])
key = target.read_cmd('r')
print_output(key)

ktp = cw.ktp.Basic()
ktp.text_len = 8
ktp.key_len = 8

# We want 3000 samples from two points
scope.adc.samples = 3000            

# Round 1 is performed at offset 73700
# Round 2 is performed at offset 131700
# Your points may be different
offsets = [73700, 131700]

# 200 traces from each run
num_traces = 200

traces = []
for _ in trange(num_traces):
    key, pt = ktp.next()
    long_trace = np.array([])
    
    # Get trace from two offsets and concatenate them
    # so we don't consume/process other data
    for i in range(len(offsets)):
        scope.adc.offset = offsets[i]
        data, trace = capture_traces('p',pt)
        long_trace = np.append(long_trace, trace)

    traces.append(cw.Trace(long_trace, pt, data[3:-2], key))

project.traces.extend(traces)
project.save()

CWbytearray(b'00 72 08 2b 7e 15 16 28 ae d2 a6 e3 00')
Cmd: r
Len: 8
Payload (hex): 2B 7E 15 16 28 AE D2 A6


  0%|          | 0/200 [00:00<?, ?it/s]

In [10]:
# Show entire trace

plot = cw.plot()
for i in range(14):
    plot *= cw.plot(project.traces[i].wave)
plot

:Overlay
   .Curve.I    :Curve   [x]   (y)
   .Curve.II   :Curve   [x]   (y)
   .Curve.III  :Curve   [x]   (y)
   .Curve.IV   :Curve   [x]   (y)
   .Curve.V    :Curve   [x]   (y)
   .Curve.VI   :Curve   [x]   (y)
   .Curve.VII  :Curve   [x]   (y)
   .Curve.VIII :Curve   [x]   (y)
   .Curve.IX   :Curve   [x]   (y)
   .Curve.X    :Curve   [x]   (y)
   .Curve.XI   :Curve   [x]   (y)
   .Curve.XII  :Curve   [x]   (y)
   .Curve.XIII :Curve   [x]   (y)
   .Curve.XIV  :Curve   [x]   (y)
   .Curve.XV   :Curve   [x]   (y)

In [11]:
# Due to slight timing variations, we need to ensure that our traces
# are synchronised. Do this here.

import chipwhisperer.analyzer as cwa

resync_traces = cwa.preprocessing.ResyncDTW(project)
resync_traces.ref_trace = 0
resync_traces.radius = 3
resync_analyzer = resync_traces.preprocess()

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 200/200 [00:02<00:00, 83.81it/s]


In [12]:
# And plot it
plt = cw.plot([])
for i in range(14):
    plt *= cw.plot(resync_analyzer.waves[i])
plt

:Overlay
   .Curve.I    :Curve   [x]   (y)
   .Curve.II   :Curve   [x]   (y)
   .Curve.III  :Curve   [x]   (y)
   .Curve.IV   :Curve   [x]   (y)
   .Curve.V    :Curve   [x]   (y)
   .Curve.VI   :Curve   [x]   (y)
   .Curve.VII  :Curve   [x]   (y)
   .Curve.VIII :Curve   [x]   (y)
   .Curve.IX   :Curve   [x]   (y)
   .Curve.X    :Curve   [x]   (y)
   .Curve.XI   :Curve   [x]   (y)
   .Curve.XII  :Curve   [x]   (y)
   .Curve.XIII :Curve   [x]   (y)
   .Curve.XIV  :Curve   [x]   (y)
   .Curve.XV   :Curve   [x]   (y)

In [13]:
# CPA for round 1
import warnings
import chipwhisperer.analyzer as cwa

from chipwhisperer.analyzer.attacks.cpa_algorithms.progressive import CPAProgressive
from chipwhisperer.analyzer.attacks.cpa_new import CPA
from chipwhisperer.analyzer.attacks.models.DES import DES, SBox_1_output

warnings.filterwarnings('ignore')

# Round 1 sbox operation starts at trace ~0
start_point= 0

# Results set
results = [[] for _ in range(2)]

leak_model = DES(model=SBox_1_output)
attack = cwa.cpa(resync_analyzer, leak_model)
attack.set_target_subkeys([0, 1, 2, 3, 4, 5, 6, 7])
attack.set_trace_source = attack.project.trace_manager()
attack.set_point_range((start_point,start_point+2200))
cb = cwa.get_jupyter_callback(attack, 8)
results[0] = attack.run(cb)

# Expected round 1 key - 22 10 30 21 32 38 07 3F

In [15]:
from textwrap import wrap
from chipwhisperer.analyzer.attacks.models.DES import DESLeakageHelper

# We now want to take the round 1 key from above,
# calculate hypothetical round 2 input
# and save it for running the round 2 attack

round_2 = cw.create_project("projects/des_round_2", overwrite = True)

des = DESLeakageHelper()

key = 0
for i, subkey in enumerate(results[0].best_guesses()):
    key |= int(subkey["guess"]) << ((7-i) * 6)

key = f'{key:048b}'

# We'll take the synced traces project for input

for trace in resync_analyzer.traces:
    pt = ''.join(f'{i:02X}' for i in trace[1])
    
    input = des.hex_to_bin(pt)
    
    # Get R1 output/R2 input
    output, _ = des.get_round_1_output(input, key)
    ct = []
    binlist = wrap(output, 8)
    for bin in binlist:
        ct.append(int(bin,2))
    
    new_trace = cw.Trace(trace[0],ct,[0]*8,[0]*8)
    round_2.traces.append(new_trace)

# Save the project
round_2.save()


In [16]:
# CPA for round 2
import warnings
warnings.filterwarnings('ignore')

import chipwhisperer.analyzer as cwa
from chipwhisperer.analyzer.attacks.models.DES import SBox_2_output

start_point=3100

leak_model = DES(model=SBox_2_output)
attack = cwa.cpa(round_2, leak_model)
attack.set_target_subkeys([0, 1, 2, 3, 4, 5, 6, 7])
attack.set_trace_source = attack.project.trace_manager()
attack.set_point_range((start_point,start_point+2500))
cb = cwa.get_jupyter_callback(attack, 8)
results[1] = attack.run(cb)

# Expected round 2 key - 16 1A 01 0A 3D 1E 1F 2A

In [17]:
# Expected round keys:
#
# round 1 key - 22 10 30 21 32 38 07 3F
# round 2 key - 16 1A 01 0A 3D 1E 1F 2A

# Calculate the full 64-bit key (parity bits are not calculated)

des = DESLeakageHelper()

key    = [[] for _ in range(2)]
binkey = ['' for _ in range(2)]

for i,k in enumerate(key):
    print(f'Best guess key (R{i+1}): ', end='')
    for subkey in results[i].best_guesses():
        key[i].append(subkey["guess"])
        print(f'{subkey["guess"]:0>2X}', end=' ')
    print()
    
    round_key = des.get_round_key(key[i],i+1,0, False)
    for bit in round_key:
        binkey[i] += str(bit).replace('?','0')


xor_round_keys = f'{int(binkey[0],2) | int(binkey[1],2):02X}'

wrap(xor_round_keys, 2)


# Expected key without parity bits set
# 2B 7E 14 16 28 AE D2 A6

Best guess key (R1): 22 10 30 21 32 38 07 3F 
Best guess key (R2): 16 1A 01 0A 3D 1E 1F 2A 


['2A', '7E', '14', '16', '28', 'AE', 'D2', 'A6']